In [65]:
import numpy as np
from scipy.optimize import curve_fit
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import matplotlib
import os
np.set_printoptions(suppress=True, formatter={'float_kind':lambda x: "%.3f" % x})

def lorentzian(x, A, x0, gamma, k, b):
    return A / (1 + ((x - x0) / gamma)**2) + k * x + b
def double_lorentzian(x, A1, x1, gamma1, A2, x2, gamma2, k, b):
    return lorentzian(x, A1, x1, gamma1, k, b) + lorentzian(x, A2, x2, gamma2, 0, 0)
def triple_lorentzian(x, A1, x1, gamma1, A2, x2, gamma2, A3, x3, gamma3, k, b):
    return lorentzian(x, A1, x1, gamma1, k, b) + lorentzian(x, A2, x2, gamma2, 0, 0) + lorentzian(x, A3, x3, gamma3, 0, 0)
%pwd
polarizations = [ "zyyz", "xyyx" ]
x = {p: np.loadtxt(f'画图/拉曼结果拟合/combined/substrate/{p}_x.txt') for p in polarizations}
y = {p: np.loadtxt(f'画图/拉曼结果拟合/combined/substrate/{p}_y.txt') for p in polarizations}

def fitting_peek(x, y, x_range, function, guess, bound):
  mask = (x > x_range[0]) & (x < x_range[1])
  x = x[mask]
  y = y[mask]
  popt, pcov = curve_fit(function, x, y, p0=guess, maxfev=100000, bounds=bound)
  return popt
fitting_init_parameter = [
  [300, 196, 1, 2e3, 204, 0.8, 0, 900],
  [300, 196, 1, 0, 900],
  [2e3, 204, 0.8, 0, 900],
  [50, 266, 5, 0, 100],
  [1e3, 611, 5, 0, 100],
  [1e4, 776, 1, 1e3, 797, 1, 1, 100],
  [1e4, 776, 1, 1e4, 782, 1, 1e3, 797, 1, 1, 100],
  [1e4, 776, 1, 1, 100],
  [1e3, 797, 1, 1, 100],
]
fitting_range = [
  [180, 220],
  [190, 199],
  [180, 220],
  [250, 280],
  [600, 617],
  [700, 850],
  [700, 850],
  [769, 783],
  [793, 803],
]
fitting_bound = [
  ([0, 192, 0, 0, 200, 0, -np.inf, -np.inf], [np.inf, 198, np.inf, np.inf, 206, np.inf, np.inf, np.inf]),
  (-np.inf, np.inf),
  (-np.inf, np.inf),
  ([0, 260, 0, -np.inf, -np.inf], [np.inf, 270, np.inf, np.inf, np.inf]),
  ([0, 605, 0, -np.inf, -np.inf], [np.inf, 617, np.inf, np.inf, np.inf]),
  (-np.inf, np.inf),
  (-np.inf, np.inf),
  (-np.inf, np.inf),
  (-np.inf, np.inf)
]

In [66]:
fig = go.Figure()
for polarization in polarizations:
  for site in range(10):
    fig.add_trace(go.Scatter(x=x[polarization][site], y=np.log(y[polarization][site]), mode='lines', name=f'{polarization} {site}'))
fig.update_layout(width=1920, height=1080)
fig.show()

In [67]:
E21_shift = {p: [None for _ in range(10)] for p in [ "zyyz", "xyyx" ]}
E21_int = {p: [None for _ in range(10)] for p in [ "zyyz", "xyyx" ]}
E22_shift = {p: [None for _ in range(10)] for p in [ "zyyz", "xyyx" ]}
E22_int = {p: [None for _ in range(10)] for p in [ "zyyz", "xyyx" ]}
for polarization in [ "zyyz", "xyyx" ]:
  for site in range(10):
    this_x = np.array(x[polarization][site])
    this_y = np.array(y[polarization][site])
    popt = fitting_peek(this_x, this_y, fitting_range[0], double_lorentzian, fitting_init_parameter[0], fitting_bound[0])
    E21_shift[polarization][site] = popt[1]
    E21_int[polarization][site] = np.abs(popt[0] * popt[2] * np.pi)
    E22_shift[polarization][site] = popt[4]
    E22_int[polarization][site] = np.abs(popt[3] * popt[5] * np.pi)
    print(f'{polarization} {site} {E21_shift[polarization][site]:.3f} {E21_int[polarization][site]:.3f} {E22_shift[polarization][site]:.3f} {E22_int[polarization][site]:.3f}')

zyyz 0 195.408 768.363 203.360 5431.550
zyyz 1 195.348 813.172 203.335 5555.979
zyyz 2 195.377 795.485 203.352 5635.418
zyyz 3 195.403 779.039 203.336 5509.505
zyyz 4 195.335 775.158 203.333 5344.158
zyyz 5 195.359 761.293 203.339 5393.468
zyyz 6 195.333 787.098 203.316 5438.928
zyyz 7 195.406 803.613 203.361 5375.814
zyyz 8 195.290 800.426 203.326 5456.324
zyyz 9 195.349 827.076 203.329 5643.830
xyyx 0 195.514 485.665 203.097 4346.026
xyyx 1 195.531 503.225 203.116 4312.411
xyyx 2 195.555 492.576 203.112 4287.793
xyyx 3 195.548 492.161 203.120 4187.482
xyyx 4 195.595 464.865 203.097 4136.669
xyyx 5 195.575 468.668 203.119 4160.958
xyyx 6 195.541 451.810 203.109 4221.797
xyyx 7 195.441 543.253 203.077 4139.015
xyyx 8 195.541 473.371 203.072 4273.308
xyyx 9 195.504 483.735 203.061 4288.090


In [68]:
A11_shift = {p: [None for _ in range(10)] for p in [ "zyyz", "xyyx" ]}
A11_int = {p: [None for _ in range(10)] for p in [ "zyyz", "xyyx" ]}
for polarization in [ "zyyz", "xyyx" ]:
  for site in range(10):
    this_x = np.array(x[polarization][site])
    this_y = np.array(y[polarization][site])
    popt = fitting_peek(this_x, this_y, fitting_range[4], lorentzian, fitting_init_parameter[4], fitting_bound[4])
    A11_shift[polarization][site] = popt[1]
    A11_int[polarization][site] = np.abs(popt[0] * popt[2] * np.pi)
    print(f'A11 {polarization} {site} {A11_shift[polarization][site]:.3f} {A11_int[polarization][site]:.3f}')
for polarization in [ "zyyz", "xyyx" ]:
  print(f'A11 {polarization} {np.mean(A11_shift[polarization]):.3f} {np.std(A11_shift[polarization]):.3f} {np.mean(A11_int[polarization]):.3f} {np.std(A11_int[polarization]):.3f}')

A11 zyyz 0 609.758 1649.677
A11 zyyz 1 609.761 1640.677
A11 zyyz 2 609.777 1684.882
A11 zyyz 3 609.754 1679.856
A11 zyyz 4 609.768 1634.458
A11 zyyz 5 609.761 1606.687
A11 zyyz 6 609.752 1586.458
A11 zyyz 7 609.768 1544.688
A11 zyyz 8 609.765 1561.382
A11 zyyz 9 609.755 1627.706
A11 xyyx 0 609.497 1759.786
A11 xyyx 1 609.503 1725.831
A11 xyyx 2 609.483 1733.897
A11 xyyx 3 609.482 1692.601
A11 xyyx 4 609.488 1680.130
A11 xyyx 5 609.504 1703.014
A11 xyyx 6 609.481 1697.842
A11 xyyx 7 609.478 1720.329
A11 xyyx 8 609.474 1791.910
A11 xyyx 9 609.476 1769.439
A11 zyyz 609.762 0.007 1621.647 44.443
A11 xyyx 609.487 0.010 1727.478 34.621


In [69]:
E23_shift = {p: [None for _ in range(10)] for p in [ "zyyz", "xyyx" ]}
E23_int = {p: [None for _ in range(10)] for p in [ "zyyz", "xyyx" ]}
for polarization in [ "zyyz" ]:
  for site in range(10):
    this_x = np.array(x[polarization][site])
    this_y = np.array(y[polarization][site])
    popt = fitting_peek(this_x, this_y, fitting_range[5], double_lorentzian, fitting_init_parameter[5], fitting_bound[5])
    E23_shift[polarization][site] = popt[1]
    E23_int[polarization][site] = np.abs(popt[0] * popt[2] * np.pi)
    print(f'E23 {polarization} {site} {E23_shift[polarization][site]:.3f} {E23_int[polarization][site]:.3f}')
for polarization in [ "xyyx" ]:
  for site in range(10):
    this_x = np.array(x[polarization][site])
    this_y = np.array(y[polarization][site])
    popt = fitting_peek(this_x, this_y, fitting_range[6], triple_lorentzian, fitting_init_parameter[6], fitting_bound[6])
    E23_shift[polarization][site] = popt[1]
    E23_int[polarization][site] = np.abs(popt[0] * popt[2] * np.pi)
    print(f'E23 {polarization} {site} {E23_shift[polarization][site]:.3f} {E23_int[polarization][site]:.3f}')

E23 zyyz 0 776.500 64818.596
E23 zyyz 1 776.500 64297.084
E23 zyyz 2 776.500 65131.301
E23 zyyz 3 776.500 64601.599
E23 zyyz 4 776.500 63119.501
E23 zyyz 5 776.500 62463.736
E23 zyyz 6 776.500 62179.213
E23 zyyz 7 776.500 60941.482
E23 zyyz 8 776.500 61402.188
E23 zyyz 9 776.500 62843.567
E23 xyyx 0 776.500 58383.753
E23 xyyx 1 776.500 57862.423
E23 xyyx 2 776.500 56686.662
E23 xyyx 3 776.500 56027.331
E23 xyyx 4 776.500 55887.896
E23 xyyx 5 776.500 56372.792
E23 xyyx 6 776.500 56010.185
E23 xyyx 7 776.500 56841.411
E23 xyyx 8 776.500 57759.439
E23 xyyx 9 776.500 57964.066


In [70]:
for polarization in [ "zyyz", "xyyx" ]:
  np.savetxt(f'画图/拉曼结果拟合/combined/substrate/E21_shift_{polarization}.txt', E21_shift[polarization], fmt='%.6f')
  np.savetxt(f'画图/拉曼结果拟合/combined/substrate/E22_shift_{polarization}.txt', E22_shift[polarization], fmt='%.6f')
  np.savetxt(f'画图/拉曼结果拟合/combined/substrate/A11_shift_{polarization}.txt', A11_shift[polarization], fmt='%.6f')
  np.savetxt(f'画图/拉曼结果拟合/combined/substrate/E23_shift_{polarization}.txt', E23_shift[polarization], fmt='%.6f')